# Capstone Project - The Battle of the Neighborhoods
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Results](#results)
* [Discussion](#discussion)
* [Conclusion](#conclusion)



## Introduction <a name="introduction"></a>

### Background

Pune is the second largest city in the Indian state of Maharashtra, after Mumbai. The city has emerged as a major educational hub in recent decades, with nearly half of the total international students in the country studying in Pune. The city has the eighth largest metropolitan economy and the sixth highest per capita income in the country. The key sectors of the local economy are education, manufacturing and information technology. The educational and economic ecosystem of the city attracts a young and vibrant metropolitan crowd.

An Italian restaurant chain wants to open a restaurant in Pune city. There are lots of restaurants in Pune. They want to find an optimal location for opening an Italian restaurant near to the city center. 


### Business Problem
The business problem here is to generate a few most promising neighborhoods in Pune to open an Italian restaurant based on some defined criterias. There are three important criterias regarding neighborhood locations:

* The locations should not already be crowded with restaurants. 
* There should not be any Italian restaurants in the vicinity. 
* The locations should be as close to the city center as possible.

We will use our data science powers to find optimal neighborhood locations based on defined criterias. We will collect, explore and analyze neighborhood locations and restaurants data to answer following four questions:
1. How many restaurants are present in a radius of 6 km around the city center? 
2. How many of the identified restaurants are Italian restaurants?
3. What are the locations within 2.5 km area with no more than two restaurants in a radius of 250 meters and without Italian restaurants in a radius of 400 meters?
4. What are the final 15 location recommendations with addresses?



## Data <a name="data"></a>

Based on definition of our problem, there are three factors that will influence our decision:
1. Number of existing restaurants in the neighborhood (any type of restaurant)
2. Number of and distance to Italian restaurants in the neighborhood, if any
3. Distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

### Data Source

Following data sources will be needed to extract/generate the required information:
* **Centers of candidate areas** will be generated algorithmically and approximate addresses of centers of those areas will be obtained using the ***GeoPy*** python library.
* **Number of restaurants and their type and location** in every neighborhood will be obtained using ***Foursquare API***
* **Coordinate of Pune center** will be obtained using ***GeoPy*** python library.

### Data Preparation

#### Neighborhood Candidates

We will generate neighborhood candidates by creating a grid of cells covering our area of interest which is aproximatly 12x12 killometers centered around the Pune city center. Then we will find latitude & longitude coordinates for centroids of our neighborhood candidate. 

#### Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [0]:
# Library to handle data in a vectorized manner
import numpy as np

# Library for data analsysis
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Library for geocoding web services
#!pip install geopy
from geopy.geocoders import Nominatim

# Library for manipulation and analysis of geometric objects in the Cartesian plane.
#!pip install shapely
import shapely.geometry

# Library for cartographic projections and coordinate transformations library
#!pip install pyproj
import pyproj

# Library for mathematical functions
import math

# Library to handle requests
import requests

# Library for map rendering library
#!pip install folium
import folium
from folium.plugins import HeatMap

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# Library for k-means clustering
from sklearn.cluster import KMeans

print('Libraries imported.')

Libraries imported.


#### Get the latitude and longitude values of Pune city.

First, we need to find geographical cooedinates of Pune city. Using GeoPy library, we will convert the address into latitude and longitude values. In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent as *pune_explorer*.

In [0]:
address = 'Pune, India'

geolocator = Nominatim(user_agent="pune_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
pune_center = [latitude, longitude]

print('The geographical coordinate of {}: {}'.format(address, pune_center))

The geograpical coordinate of Pune, India: [18.521428, 73.8544541]


#### Create a grid of area candidates centered around Pune city centre.

Now we will create a grid of neighborhood area candidates which is equaly spaced and centered around the city center. Thses candidate areas will be within ~6km from Pune city center. 

We will define neighborhoods as circular areas with a radius of 300 meters. Distance between two neighborhood centers will be 600 meters.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. 

So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters). Please note UTM zone for Pune is 43.

In [0]:
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=43, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=43, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Pune center longitude={}, latitude={}'.format(pune_center[1], pune_center[0]))
x, y = lonlat_to_xy(pune_center[1], pune_center[0])
print('Pune center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Pune center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Pune center longitude=73.8544541, latitude=18.521428
Pune center UTM X=379084.4523924125, Y=2048259.8861715223
Pune center longitude=73.8544541, latitude=18.521427999999997


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [0]:
# City center in Cartesian coordinates
pune_center_x, pune_center_y = lonlat_to_xy(pune_center[1], pune_center[0])

k = math.sqrt(3) / 2 # vertical offset for hexagonal grid cells
x_min = pune_center_x - 6000
x_step = 600
y_min = pune_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(pune_center_x, pune_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


#### Visualize area candidates grid on Pune city map 

Using Folium library, we will generate map for Pune and visualize city center location and candidate neighborhood centers on the map.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.Marker(pune_center, popup='Pune').add_to(map_pune)
for lat, lon in zip(latitudes, longitudes):
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_pune)

map_pune

#### Get approximate addresses of centers of candidate areas.

Now we have the coordinates of centers of equally spaced candidate areas within ~6km from Pune city center. 

Let's use GeoPy to get approximate addresses of those locations.

In [0]:
def get_address(latitude, longitude, verbose=False):
    try:
        geolocator = Nominatim(user_agent="pune_explorer")
        lat_long_str = str(latitude) + ', ' + str(longitude)
        location = geolocator.reverse(lat_long_str)
        address = location.address
        return address
    except:
        return None

addr = get_address(pune_center[0], pune_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(pune_center[0], pune_center[1], addr))

Reverse geocoding check
-----------------------
Address of [18.521428, 73.8544541] is: Shaniwar Peth, Pune, Pune City, Pune District, Maharashtra, 411001, India


In [0]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Pune City, Pune District, Maharashtra', '')
    address = address.replace(', India', '')
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [0]:
addresses[150:170]

['Prince Of Wales Drive, Suyojan Society, Fatima Nagar, Pune, 411001',
 'Empress Garden View Society, Fatima Nagar, Pune, 411001',
 'Fatima Nagar, Pune, 411001',
 'Sneh Paradise, Kothrud, Pune, 411038',
 'Sneh Paradise, Kothrud, Pune, 411038',
 'NO ADDRESS',
 'Sneh Paradise, Erandwana, Pune, 411001',
 'ILS Law College, Kanchangalli, Sneh Paradise, Erandwana, Pune, 411001',
 'Dattatray Annaji Gangote Path, Sneh Paradise, Deccan Gymkhana, Pune, 411004',
 'Kashibai Vishnu Sane Path, Deccan Gymkhana, Pune, 411004',
 'Marne Paan House, Jangli Maharaj Path, Deccan Gymkhana, Pune, 411004',
 'NO ADDRESS',
 'Tambdi Jogeshwari, Nakalakar Bhonde Path, Narayan Peth, Pune, 411001',
 'Ganesh Peth, Pune, 411001',
 'Ganesh Peth, Pune, 411001',
 'Shahu Swiming Pool, Quarter Gate, Ganesh Peth, Pune, 411001',
 'Dastur Meher Road, Pune Cantonment, Pune, 411001',
 'NO ADDRESS',
 'Suyojan Society, Pune Cantonment, Pune, 411001',
 'Suyojan Society, Ghorpuri, Pune, 411001']

#### Convert addresses list into a pandas data frame.

We will create a Pandas dataframe form address list with 6 columns: Address, Latitude, Longitude, X, Y, and Distance from center.

In [0]:
df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  Sinhagad College Wadgaon Campus, Sinhgad Cante...  18.469675  73.837752   
1                          Tukai Nagar, Pune, 411001  18.469709  73.843434   
2                        Sahakar Nagar, Pune, 411001  18.469744  73.849116   
3                        Sahakar Nagar, Pune, 411001  18.469778  73.854797   
4  KK Market, KK Market road, Sahakar Nagar, Pune...  18.469813  73.860479   
5                        Sahakar Nagar, Pune, 411001  18.469847  73.866161   
6                              Kondhwa, Pune, 411018  18.469881  73.871843   
7      Prosperity Society, Tukai Nagar, Pune, 411001  18.474317  73.829198   
8      Prosperity Society, Tukai Nagar, Pune, 411001  18.474352  73.834879   
9      Prosperity Society, Tukai Nagar, Pune, 411001  18.474387  73.840561   

               X             Y  Distance from center  
0  377284.452392  2.042544e+06           5992.495307  
1  377884.452392  2.042544e+06           5840.376700  
2  378484.452392  2.042544e+06           5747.173218  
3  379084.452392  2.042544e+06           5715.767665  
4  379684.452392  2.042544e+06           5747.173218  
5  380284.452392  2.042544e+06           5840.376700  
6  380884.452392  2.042544e+06           5992.495307  
7  376384.452392  2.043064e+06           5855.766389  
8  376984.452392  2.043064e+06           5604.462508  
9  377584.452392  2.043064e+06           5408.326913

#### Get restaurants info in each neighborhood use Foursquare API.

Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

Define Foursquare Credentials and Version.

In [1]:
LIMIT = 100

CLIENT_ID = '<CLIENT_ID>'
CLIENT_SECRET = '<CLIENT_SECRET>'
VERSION = '20180605'

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: <CLIENT_ID>
CLIENT_SECRET:<CLIENT_SECRET>


Get category IDs corresponding to Italian restaurants from [Foursquare web site]((https://developer.foursquare.com/docs/resources/categories)).

In [0]:
food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

Define a function to get categories.

In [0]:
def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

Define a function to check if a category is restaurant with specific filter.

In [0]:
def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

Define a function to format address of a location.

In [0]:
def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Pune 411038', '')
    address = address.replace(', Mahārāshtra, India', '')
    return address

Define a function to get venues near a location.

In [0]:
def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

Define a function to get restaurants nearby a neighborhood location.

In [0]:
def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage
        venues = get_venues_near_location(lat, lon, 
                                          food_category, 
                                          CLIENT_ID, 
                                          CLIENT_SECRET, 
                                          radius=350, 
                                          limit=100)
        area_restaurants = []

        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]

            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)

            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])

                restaurant = (venue_id, venue_name, 
                              venue_latlon[0], venue_latlon[1], 
                              venue_address, 
                              venue_distance, 
                              is_italian, 
                              x, y)

                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                
                restaurants[venue_id] = restaurant
                
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    
    return restaurants, italian_restaurants, location_restaurants

Get restaurants info using above defined functions

In [0]:
restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.
Total number of restaurants: 552
Total number of Italian restaurants: 24
Percentage of Italian restaurants: 4.35%
Average number of restaurants in neighborhood: 1.3214285714285714


**List of all restaurants**

In [0]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4df6cc2ed1642d7385a4e441', 'Mandar Gardens', 18.469663006328517, 73.83475866608136, 'Vadgaon Bk., Pune', 316, False, 376968.35413793847, 2042544.8799034164)
('4ed892926da1642c5a76a80f', 'Picante - pure veg', 18.46708275760659, 73.83625771773013, 'Vadgaon, Pune', 328, False, 377124.81116065994, 2042258.3305106594)
('4f8ae6aae4b05ae88a2ab1e0', 'dosa camp', 18.46762582099172, 73.86461693853506, 'India', 296, False, 380119.85172350984, 2042299.3906009383)
('520a62eb498e0d434f56b49c', "Rutu's Garden", 18.46904077991037, 73.87079592663869, 'India', 144, False, 380773.30998865026, 2042451.8831624943)
('5193b45b498e81da73c002a6', 'Woodlands Veg Delight', 18.474824190379973, 73.8561865558626, 'Next To Padmavati Bus Stand, Pune', 154, False, 379234.66846458067, 2043101.5666290747)
('50043b18e4b031e9cc29b65a', 'Shailaja Catering', 18.47402113626089, 73.8578175300253, 'India', 56, False, 379406.3257989411, 2043011.6123900153)
('5703e5eb498eef61abf2

**List of Italian restaurants**

In [0]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('56e7db0f498e7b87085c1324', 'Little Italy', 18.48988915254892, 73.88654112956714, 'Lullanagar (Near Gera Junction), Pune', 266, True, 382450.14501170395, 2044748.622461986)
('4e4e815bfa7626401e9bc2fc', 'Metromix', 18.498506701001073, 73.80193175848053, 'Kumar Parisar, India', 188, True, 373523.09766017605, 2045759.4083245916)
('50dc3917e4b0992ed69b0b09', 'Feesta', 18.508699058847625, 73.8125012948326, 'shop number 5, Rahul Complex (Paud Road, Kothrud)', 348, True, 374646.4447236718, 2046879.933286976)
('4c677a20b80abe9ab46ad0e5', 'By The Way', 18.525058508695786, 73.84154053093603, '6a 1195/C, Next To Tukaram Paduka Mandir, Opposite National Heart Institute (Fergusson College Road, Shivaji Nagar), Pune 411005', 194, True, 377723.82186215266, 2048670.3474119524)
('4d1ca1551356224be0f310be', 'Alto Vino', 18.53197888529939, 73.82979570889925, 'Level 1, JW Marriott (Senapati Bapat Road), Pune', 179, True, 376488.9811750529, 2049444.1

**Restaurants around location**

In [0]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Abhishek Veg, Purepur Kolhapur, Manali, Pavitra pure veg, Abhishek Non Veg
Restaurants around location 102: Harvest Club, Multi Spice, Vishnu Ji Ki Rasoi, Aswan
Restaurants around location 103: Grace Biryani House
Restaurants around location 104: 
Restaurants around location 105: Atharva hotel, sarasbaug chowpati
Restaurants around location 106: Sahil Hotel, Hotel Natraj
Restaurants around location 107: 
Restaurants around location 108: Chandan restaurant
Restaurants around location 109: In Green
Restaurants around location 110: 


#### Visualize all the collected restaurants on the map.

Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.Marker(pune_center, popup='Pune').add_to(map_pune)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_pune)

map_pune

So now we have all the restaurants in area within few kilometers from Pune city center and which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant in Pune!

## Methodology <a name="methodology"></a>

In this project, our objective is to find and recommend an optimal location for opening an Italian restaurant in Pune city, India.

The optimal location for a restaurant is an area with low restaurant density, specifically Italian restaurants. We will try to find such areas in the Pune city. We will limit our analysis to area ~6km around the city center.

We will follow four steps methodology:
1. **Data collection and preparartion**

  In first step, we have collected and prepared the required data: location and type (category) of every restaurant within 6km from Pune city center. We have also identified Italian restaurants according to Foursquare categorization.

2. **Data analysis** 

  In the second step, we will explore and analyze our retaurants data to calculate '*restaurant density*' across different areas of Pune. We will use *heatmaps* to identify a few promising areas close to center with low number of restaurants in general and no Italian restaurants in the vicinity. 

3. **Clustering**

  In the third and final step, we will focus on the most promising areas. We will create clusters of locations that meet some basic requirements established in discussion with stakeholders.

  There are two basic requirements of optimal location that we will take into consideration:
  * locations with no more than two restaurants in radius of 250 meters, and
  * locations without Italian restaurants in radius of 400 meters. 

4. **Results** 
  
  We will present map of all promising locations. We will also provide clusters of those locations to identify neighborhoods which should be a starting point for final 'street level' exploration and search for the optimal venue location by stakeholders.

### Data Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data.

#### Count the number of restaurants in every area candidate.

In [0]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 1.3214285714285714


Address   Latitude  Longitude  \
0  Sinhagad College Wadgaon Campus, Sinhgad Cante...  18.469675  73.837752   
1                          Tukai Nagar, Pune, 411001  18.469709  73.843434   
2                        Sahakar Nagar, Pune, 411001  18.469744  73.849116   
3                        Sahakar Nagar, Pune, 411001  18.469778  73.854797   
4  KK Market, KK Market road, Sahakar Nagar, Pune...  18.469813  73.860479   
5                        Sahakar Nagar, Pune, 411001  18.469847  73.866161   
6                              Kondhwa, Pune, 411018  18.469881  73.871843   
7      Prosperity Society, Tukai Nagar, Pune, 411001  18.474317  73.829198   
8      Prosperity Society, Tukai Nagar, Pune, 411001  18.474352  73.834879   
9      Prosperity Society, Tukai Nagar, Pune, 411001  18.474387  73.840561   

               X             Y  Distance from center  Restaurants in area  
0  377284.452392  2.042544e+06           5992.495307                    0  
1  377884.452392  2.042544e+06           5840.376700                    0  
2  378484.452392  2.042544e+06           5747.173218                    0  
3  379084.452392  2.042544e+06           5715.767665                    0  
4  379684.452392  2.042544e+06           5747.173218                    0  
5  380284.452392  2.042544e+06           5840.376700                    1  
6  380884.452392  2.042544e+06           5992.495307                    1  
7  376384.452392  2.043064e+06           5855.766389                    0  
8  376984.452392  2.043064e+06           5604.462508                    0  
9  377584.452392  2.043064e+06           5408.326913                    0

#### Calculate the distance to nearest Italian restaurant from every area candidate center.

In [0]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_locations['Distance to Italian restaurant'] = distances_to_italian_restaurant

df_locations.head(10)

Address   Latitude  Longitude  \
0  Sinhagad College Wadgaon Campus, Sinhgad Cante...  18.469675  73.837752   
1                          Tukai Nagar, Pune, 411001  18.469709  73.843434   
2                        Sahakar Nagar, Pune, 411001  18.469744  73.849116   
3                        Sahakar Nagar, Pune, 411001  18.469778  73.854797   
4  KK Market, KK Market road, Sahakar Nagar, Pune...  18.469813  73.860479   
5                        Sahakar Nagar, Pune, 411001  18.469847  73.866161   
6                              Kondhwa, Pune, 411018  18.469881  73.871843   
7      Prosperity Society, Tukai Nagar, Pune, 411001  18.474317  73.829198   
8      Prosperity Society, Tukai Nagar, Pune, 411001  18.474352  73.834879   
9      Prosperity Society, Tukai Nagar, Pune, 411001  18.474387  73.840561   

               X             Y  Distance from center  Restaurants in area  \
0  377284.452392  2.042544e+06           5992.495307                    0   
1  377884.452392  2.042544e+06           5840.376700                    0   
2  378484.452392  2.042544e+06           5747.173218                    0   
3  379084.452392  2.042544e+06           5715.767665                    0   
4  379684.452392  2.042544e+06           5747.173218                    0   
5  380284.452392  2.042544e+06           5840.376700                    1   
6  380884.452392  2.042544e+06           5992.495307                    1   
7  376384.452392  2.043064e+06           5855.766389                    0   
8  376984.452392  2.043064e+06           5604.462508                    0   
9  377584.452392  2.043064e+06           5408.326913                    0   

   Distance to Italian restaurant  
0                     4948.320729  
1                     5070.048006  
2                     4537.240972  
3                     4023.397134  
4                     3536.791392  
5                     3090.317494  
6                     2703.928821  
7                     3931.159158  
8                     4387.213011  
9                     4816.146590

#### Calculate average distance to the closest Italian restaurant from each area center.

In [0]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 1725.1978236869963


Now let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show a few circles on the map indicating distance of 1km, 2km and 3km from Pune city center.

#### Get latitude and longitude of all restaurants and Italian ones.

In [0]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

#### Create a map showing heatmap of density of restaurants.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_pune) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(pune_center, radius=1000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=2000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=3000, fill=False, color='white').add_to(map_pune)

map_pune

Looks like a few pockets of low restaurant density closest to city center can be found **north, north-east and south-east from Pune city center**. 

Let's create another heatmap map showing **heatmap/density of Italian restaurants** only.

#### Create a heatmap showing density of Italian restaurants only.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_pune) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(pune_center, radius=1000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=2000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=3000, fill=False, color='white').add_to(map_pune)

map_pune

This map is not so 'hot'. It indicates higher density of existing Italian restaurants directly north-east and north-west from Pune center. Closest pockets of **low Italian restaurant density positioned north, south, south-east and south-west from the city center**.

Based on this analysis, we will now focus our analysis on areas *north, south, south-west and south-east from Pune city center*. We will move reduce the size of our area of interest to have a radius of **2.5km**.

#### Create a heatmap showing density of restaurants within 2.5km area.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(pune_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_pune)

map_pune

This map nicely covers all the pockets of low restaurant density closest to Pune city center.

Now, let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

#### Create a new dense grid of location candidates.

In [0]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
roi_x_min = pune_center_x - 2500
x_step = 100
roi_y_min = pune_center_y - 2500
y_step = 100 * k 

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(pune_center_x, pune_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant**.

Define a function to count nearby restaurants.

In [0]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

#### Define a function to find rearest restaurant.

In [0]:
def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

#### Generate data of location candidates.

In [0]:
roi_restaurant_counts = []
roi_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    roi_italian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


#### Convert location candidates data into a Pandas data frame. 

In [0]:
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Italian restaurant':roi_italian_distances})

df_roi_locations.head(10)

Latitude  Longitude              X             Y  Restaurants nearby  \
0  18.498834  73.854131  379034.452392  2.045760e+06                   3   
1  18.498840  73.855078  379134.452392  2.045760e+06                   3   
2  18.499585  73.848916  378484.452392  2.045846e+06                   0   
3  18.499591  73.849864  378584.452392  2.045846e+06                   0   
4  18.499597  73.850811  378684.452392  2.045846e+06                   0   
5  18.499602  73.851758  378784.452392  2.045846e+06                   0   
6  18.499608  73.852705  378884.452392  2.045846e+06                   1   
7  18.499614  73.853652  378984.452392  2.045846e+06                   2   
8  18.499620  73.854599  379084.452392  2.045846e+06                   2   
9  18.499625  73.855546  379184.452392  2.045846e+06                   2   

   Distance to Italian restaurant  
0                     3191.948781  
1                     3234.294842  
2                     2924.506242  
3                     2952.094658  
4                     2982.782086  
5                     3016.473948  
6                     3053.070780  
7                     3092.469449  
8                     3134.564307  
9                     3179.248261

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 400 meters**.

#### Filter out locations with above mentioned constraints. 

In [0]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Italian restaurant']>=400)
print('Locations with no Italian restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 1807
Locations with no Italian restaurants within 400m: 2000
Locations with both conditions met: 1635


Let's see how this looks on a map.

#### Create a map showing filtered locations.

In [0]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_pune = folium.Map(location=pune_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_pune)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Circle(pune_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune) 

map_pune

Now we have a bunch of locations fairly close to Pune city center mostlt in north, south, south-east and south-west areas. We know that each of these locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 400m. Any of these locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap.

#### Create a map showing heatmap of good locations.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)

map_pune

Looking good! What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

#### Cluster good locations using k-means clustering.

In [0]:
number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_pune = folium.Map(location=pune_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_pune)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Circle(pune_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)

map_pune

These clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters.

#### Create a city map showing best possible locations as shaded areas.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=14)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_pune) 

map_pune

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

#### Get addresses of centers of recommended areas.

In [0]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(lat, lon).replace(', Pune City, Pune District, Maharashtra, 411001, India', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, pune_center_x, pune_center_y)
    print('{}{} => {:.1f}km from Pune'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

Mokshagundam Vishweshvarayya Flyover, Shivajinagar, Pune => 1.2km from Pune
Hamalwada Parking, Bhat Bol, Narayan Peth, Pune    => 0.8km from Pune
Swargate, Pune                                     => 2.1km from Pune
Timber Market, Ganesh Peth, Pune                   => 2.1km from Pune
Abasaheb Garware College, Karve Road, Deccan Gymkhana, Pune, Pune City, Pune District, Maharashtra, 411004, India => 2.0km from Pune
Krushi Mahavidyalay, Ganeshkhind Road, Model Colony, Pune => 1.9km from Pune
Ganesh Peth, Pune                                  => 1.8km from Pune
Shivajinagar, Pune                                 => 2.1km from Pune
Sangamwadi Road, Mangalwar Peth, Pune, Pune City, Pune District, Maharashtra, 411011, India => 2.0km from Pune
Madhavrao Peshve Marg, Dattawadi, Pune             => 2.1km from Pune
Shivajinagar, Pune                                 => 0.6km from Pune
Mangalwar Peth, Pune, Pune City, Pune District, M

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 4km from Pune city center, and about half of those less than 2km from Pune city center). 

Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. 

Most of the zones are located in <>, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

#### Create a city map showing all recommended 15 locations.

In [0]:
map_pune = folium.Map(location=pune_center, zoom_start=14)
folium.Circle(pune_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_pune)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_pune)

map_pune

## Results and Discussion <a name="results"></a>

Our data analysis shows that there is a good number of restaurants in Pune, 552 in our initial area of interest which was in a radius of 6 km around Pune city center. However there are pockets of low restaurant density fairly close to the city center. Highest concentration of restaurants is detected north-east and north-west from the city center, so we focused our attention to areas south, south-east, south-west and north.

We further narrowed down our area of interest with a radius of 2.5 km around Pune city center. We first created a dense grid of location candidates, spaced 100 m apart. These locations are then filtered such that the locations with more than two restaurants in a radius of 250 m and with an Italian restaurant closer than 400m were removed.

These location candidates were then clustered to create zones of interest which contain the greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing the largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. 

This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Pune city center but not crowded with existing restaurants (particularly Italian). It is entirely possible that there is a very good reason for a small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Pune areas close to the city center with low number of restaurants, particularly Italian restaurants, in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. 

By calculating restaurant density distribution from Foursquare data we have first identified general locations that justify further analysis, and then generated an extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. 

Clustering of those locations was then performed in order to create major zones of interest containing greatest number of potential locations and addresses of these zone centers were created to be used as starting points for final exploration by stakeholders.

Final decision on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise or proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.